# Neurális Nyelvfeldolgozás
## Alapfogalmak
* __szótár__: előre kiválasztott szavak listája
   * mérete tipikusan $10^5$, ragozó nyelveknél $10^6$, nagyságrendű.
   * __OOV__: out-of-vocabulary, az ebben nem szereplő szó
* __tokenizálás__: szöveg szavakra bontása
```
    A "Glass" című film rendezője M. Night Shyamalan.
    A " Glass " című film rendezője M. Night <UNK> .
```

### Mit szeretnénk?
Mit szoktak csinálni _nyelvfeldolgozás_ néven?
* szófajcimkézés
  * adott mondatban minden szóra egy szófajok feletti eloszlást
```
   The Option draws on modules from all the ...
   DT    NN    VBZ  IN   NNS    IN  PDT  DT
```
* nyelvmodellezés
  * adott szóra egy szótár feletti eloszlás _"melyik szó kerül arra helyre?"_
  * előre haladó (egyoldali): `The quick brown _?_`
  * kétoldali: `The quick brown _?_ jumped over the`
* fordítás
  * mondathoz mondatot rendelő rendszer
```
I am a student -> Je suis étudiant
```
* válasz generálás
  * mondathoz mondatot rendel
```
-- Láttad tegnap a meccset?
-- Igen, jól kikapott a Fradi!
```

## A szöveg
A (neurális) képfelismereshez képest két lényeges és megkerülhetetlen különbség van:
1. egy szót hogyan reprezentáljunk
  * lehet egyszerűen a szótárban elfoglalt helyével (id), egy egész számmal
1. Változó a bemenet (vagy kimenet) hossza.
  * Nem lehet egy mondatot _átméretezni_ úgy, mint egy képet.

### Szóvektorok
* word2vec
* one-hot-vector (nem túl hatékony)
* A kettő ekvivalens egy neurális hálóban

Ezzel az 1. problémát megoldottuk, és a szóvektorok lehetnek egy neurális háló bemenetei.

## Neurális architektúrák
Hogyan oldjuk meg, hogy változó hosszú bemenetet kapjon a neurális hálónk (egy bemeneti egység egy szóvektor).

Ráadásul egy mondatban a szavak közti kapcsolat messze ívelhet (long-range dependencies).

* konvolúció, fix ablak
   * a word2vec is ilyen
```
   [_ _ The quick brown] fox jumped over the`
   [_ The quick brown fox] jumped over the`
   [The quick brown fox jumped] over the`
   The [quick brown fox jumped over] the`
```
* rekurrencia, __RNN__
* [Attention](https://arxiv.org/pdf/1508.04025.pdf)

## RNN
http://www.wildml.com/2015/09/recurrent-neural-networks-tutorial-part-1-introduction-to-rnns/

Legyen $\underline{x}:V\mapsto \mathbb{R}^d$ egy szóbeágyazás (a szóhoz szóvektort rendelő függvényünk).

Legyen $\underline{s}\in\mathbb{R}^n$ egy belső reprezentáció, ami a mondatról a neurális háló fejében él.
* üres mondatra $\underline{s}_0=\underline{0}$
* Egyetlen szavas mondatra, legyen  $\underline{s}_0 = \operatorname{layer}(\underline{x}_1)$
$$
\operatorname{layer}(\underline{x}) = \sigma(U\cdot \underline{x} + \underline{b})
$$
  De egy réteg maga másmilyen is lehet.
* $\underline{s}_t = f(\underline{s}_{t-1}, \underline{x}_t)$
$$
f(\underline{s}_{t-1}, \underline{x}_t) = \sigma(W\cdot \underline{s}_{t-1} + U\cdot \underline{x}_t)
$$
* $U$ mátrix mondja meg, hogy a soron következő szó vektorát hogyan vegyük figyelembe
* $W$ a rekurrencia mátrix
$$
\underline{s}_t = f(f(\underline{s}_{t-2}, \underline{x}_{t-1}), \underline{x}_t)
$$
$$
\underline{s}_t = \underbrace{f(f(\ldots f}_{t \text{ times}}(\underline{0}, \underline{x}_1) \ldots, \underline{x}_{t-1}), \underline{x}_t)
$$

Figyeljük meg, hogy ez a leképezés adott $t$-re deriválható $W, U, \underline{x}$ szerint!
* __backpropagation through time__
* unroll
* deep, mély a háló, de időben és nem térben.

### RNN réteg
* Legyen egy $V^T$ mondatunk
  * $T$ hosszú, minden eleme $V$-nek egy eleme (szó)
  * Ehhez rendeltünk egy $\mathbb{R}^{T\times n}$ mátrixot, melynek minde sora az abban az időpillanatra vonatkozó $\underline{s}$ vektor.
  * Egy sora, az addig elhangzott (leírt) mondat summázata: vektor reprezentációja.
* Erre már csak egy feladat függő réteget kell rakni
  * Minden $1\leq t \leq T$ időpillanatban egy softmax réteg, mégpedig ugyan azokkal a súlyokkal.
$$
\underline{o}_t = \operatorname{layer}(\underline{s}_t)
$$
* Nyelvmodellezésben az elvárt kimenet a bemenet eltoltja.

#### Változatok
* bi-directional
* gated ([GRU](https://arxiv.org/pdf/1704.08430.pdf), [LSTM](https://en.wikipedia.org/wiki/Long_short-term_memory))
* több RNN réteg egymáson

### Mondat fordítás
* Ha a kimenet egy mondat, esetleg más szótárú mint a bemenet és más hosszúságú is lehet
* Előbb megrágjuk a bemeneti mondatot, abból lesz egy $\underline{s}_{T_\text{bemenet}}$
* Ezt beadjuk egy másik RNN-nek a kezdeti állapotául
$$
\underline{s}_{\text{kimenet}, 0} = \underline{s}_{\text{bemenet}, T_\text{bemenet}}
$$
  Ezután a kimeneti háló egy másik RNN.
* Matematikailag: a fordítás a kimeneti mondat nyelvmodellje, ahol feltételezünk a bemeneti mondatra.
  $$
  f(\text{bemeneti mondat}) = \operatorname{argmax}_{\text{kimeneti mondat}}\mathbb{P}\left(\text{kimeneti mondat}\mid \text{bemeneti mondat}\right)
  $$


#### generálás
Adott (félig befejezett) mondat befejezése.

* Legyen $\underline{s}_t$ egy adott állapota egy (félig befejezett) mondatnak
* $\underline{o}_{t} = \operatorname{argmax}(\operatorname{layer}(\underline{s}_t))$
* $\underline{s}_{t+1} = \underline{o}_{t}$
* __beam search__

## További irányok
* attention
* transformer [attention is all you need](https://arxiv.org/abs/1706.03762)
* videó, mint képet sorozata
  * video captioning
* hangfelismerés